# Snowpack and Streamflow Conditions

This section describes the seasonal snowpack conditions in the watersheds. This information will be updated throughout the winter season. You will also find detailed information on streamflow conditions in the watersheds

In [1]:
# Import libraries
import pandas as pd
import os
import numpy as np
import matplotlib.pyplot as plt
import altair as alt
import altair_saver 

In [2]:

os.chdir('C://Users/pmarshal/Documents/Climate-Outlook/monthly-climate')
os.getcwd()

'C:\\Users\\pmarshal\\Documents\\Climate-Outlook\\monthly-climate'

## 2023-2024 Snow Summary

Higher terrain in the watersheds were blanketed in early season snow on October 25-26 as a low pressure system off the Pacific clashed with a surge of Arctic air from the north. The front side (near the ski areas) received 30-40 cm of snow, with less snow further north. Most of this snow had melted by the end of October. 

```{figure} img/Orchid_lake_Snow.jpg
---
name: orchid_snow
---
Fresh snow at Orchid Lake (1200m) on October 25
```

In [3]:
snow = pd.read_csv('data/orchid_snow.csv', parse_dates=['date']) 
snow['year'] = pd.DatetimeIndex(snow['date']).year
snow['month'] = pd.DatetimeIndex(snow['date']).month
snow['day'] = pd.DatetimeIndex(snow['date']).day
snow['DOY'] = pd.DatetimeIndex(snow['date']).dayofyear

In [4]:
# Claculate statistics on mean temp column
snow['mean'] = snow.groupby('wtr_day_year')['depth'].transform('mean').round(1)
snow['max'] = snow.groupby('DOY')['depth'].transform('max')
snow['min'] = snow.groupby('DOY')['depth'].transform('min')
snow['std'] = snow.groupby('DOY')['depth'].transform('std')
snow['sem'] = snow.groupby('DOY')['depth'].transform('sem')
snow['ci95_hi'] = snow['mean'] + 1.96* snow['sem']
snow['ci95_lo'] = snow['mean'] - 1.96* snow['sem']

In [5]:
# Create dataframe with data for the current year
snow_2024 = snow.loc[snow['wtr_year'] == 2024]
snow_2023 = snow.loc[snow['wtr_year'] == 2023]

In [6]:
# Create dataframe with historical data (i.e. not == current year)
past = snow.loc[snow['wtr_year'] != 2023]

In [7]:
past_stats = past.loc[336:700]

In [8]:
# Calculate past low temperatures
pastlow = past.groupby('DOY')['depth'].transform('min')
pastlow = pastlow.reset_index()
pastlow = pastlow.loc[0:364]
pastlow['DOY'] = past['DOY']
pastlow = pastlow.rename(columns={"depth": "low"})

In [9]:
# Calculate past high temperatures
pasthigh = past.groupby('DOY')['depth'].transform('max')
pasthigh = pasthigh.reset_index()
pasthigh = pasthigh.loc[0:364]
pasthigh['DOY'] = past['DOY']
pasthigh = pasthigh.rename(columns={"depth": "high"})

In [10]:
plot_2023 = alt.Chart(snow_2024).mark_line(color='red', strokeWidth=2).encode(
    alt.X('wtr_day_year'),
    alt.Y('depth'),
    tooltip=[alt.Tooltip('monthdate(date):T', title="Date"), alt.Tooltip('depth:Q', title="Snow Depth")]
)

The chart below shows the daily average snow depth at Orchid Lake. The current year (2023/24) is shown in red, along with the average (gray line), range of normal (gray shaded area), and the range of maximum and minimum (blue shaded area). The data record for this station dates back to October 2006. 

In [11]:
alt.data_transformers.disable_max_rows()

title = alt.TitleParams(
   text='Orchid Lake Weather Station - 1175 m',
   subtitle="Snow Depth (2006/07 - 2023/24)",
   anchor='middle',
   fontSize=14,
   fontWeight='bold')

area = alt.Chart(past_stats, title=title).mark_area(color='#7DA6F3', opacity=0.5).encode(
    alt.X('wtr_day_year', title='Date - Oct 1(0) to Sep 30(365)', scale=alt.Scale(domain=[0,320], nice=False)),
    alt.Y('max:Q', title='Snow Depth (cm)', scale=alt.Scale(domain=[0,700])),
    alt.Y2('min:Q')
).properties(width=600, height=300)

area2 = alt.Chart(past_stats).mark_area(color='#919397', opacity=0.6).encode(
    alt.X('wtr_day_year', scale=alt.Scale(domain=[0,320], nice=False)),
    alt.Y('ci95_hi:Q'),
    alt.Y2('ci95_lo:Q')
)

wmean = alt.Chart(snow).mark_line(color= "black", opacity=0.6, strokeDash=[4, 2]).encode(
    alt.X('wtr_day_year', title='Date - Oct 1(0) to Sep 30(365)', scale=alt.Scale(domain=[0,320], nice=False)),
    alt.Y('mean', title='Snow Depth (cm)'),
    tooltip=[alt.Tooltip('monthdate(date):T', title="Date"), alt.Tooltip('mean:Q', title="Mean Depth") , alt.Tooltip('wtr_day_year', title="Day of Water Year")]
)

wyear_2023 = alt.Chart(snow[snow['wtr_year'] == 2023]).mark_line(color= "violet", opacity=0.6).encode(
    alt.X('wtr_day_year', title='Date - Oct 1(0) to Sep 30(365)', scale=alt.Scale(domain=[0,320], nice=False)),
    alt.Y('depth', title='Snow Depth (cm)')
)

area + area2  + wmean + wyear_2023 + plot_2023.interactive()

alt.LayerChart(...)

## Streamflow Conditions
This next section focuses on streamflow levels at the Capilano River above Lakehead (08GA010) gauge. During the fall and winter season, the focus is on high flows (storm response).

In [12]:
# Import dataset
flow = pd.read_csv('data/cap_flows.csv', parse_dates=['date']) 
flow['year'] = pd.DatetimeIndex(flow['date']).year
flow['month'] = pd.DatetimeIndex(flow['date']).month
flow['day'] = pd.DatetimeIndex(flow['date']).day
flow['DOY'] = pd.DatetimeIndex(flow['date']).dayofyear


In [13]:
# Claculate statistics on mean temp column
flow['mean'] = flow.groupby('DOY')['flow'].transform('mean')
flow['max'] = flow.groupby('DOY')['flow'].transform('max')
flow['min'] = flow.groupby('DOY')['flow'].transform('min')
flow['std'] = flow.groupby('DOY')['flow'].transform('std')
flow['sem'] = flow.groupby('DOY')['flow'].transform('sem')
flow['ci95_hi'] = flow['mean'] + 1.96* flow['sem']
flow['ci95_lo'] = flow['mean'] - 1.96* flow['sem']

In [14]:
# Create dataframe with data for the current year
current_year = flow.loc[flow['year'] == 2023]

In [15]:
# Create dataframe with historical data (i.e. not == current year)
past = flow.loc[flow['year'] != 2023]

In [16]:
past_stats = past.loc[0:364]

The plot below shows average daily inflows for 2023 (blue line), average daily flows (dashed line), and the range of normal (shaded area). 

In [72]:
alt.data_transformers.disable_max_rows()

rule = alt.Chart(pd.DataFrame({
  'flow': ['240'],
  'color': ['gray']
})).mark_rule(opacity=0.8, strokeDash=[3,3]).encode(
  y='flow:Q',
  color=alt.Color('color:N', scale=None)
)

title = alt.TitleParams(
   text='Capilano River at Lakehead (08GA010)',
   subtitle="Mean Daily Inflows",
   anchor='middle',
   fontSize=14,
   fontWeight='bold')

year_2023 = alt.Chart(flow[flow['year'] == 2023], title=title).mark_line(color= "darkblue", size= 2).encode(
    alt.X('monthdate(date):T', title=None),
    alt.Y('flow:Q', title='Inflow (m^3/s)', scale=alt.Scale(domain=[0, 250])),
    tooltip=["year:N", "flow"],
)

mean = alt.Chart(past).mark_line(color='black', opacity=0.6, strokeDash=[4, 2], size= 1).encode(
    alt.X('monthdate(date):T', title=None),
    alt.Y('mean(flow):Q', title='Inflow (m^3/s)')
)

area2 = alt.Chart(past_stats).mark_area(color='#919397', opacity=0.6).encode(
    alt.X('monthdate(date)'),
    alt.Y('ci95_hi:Q'),
    alt.Y2('ci95_lo:Q')
)


#area2 + mean + year_2023 + rule.properties(width=600).interactive()

In [71]:

text = alt.Chart(pd.DataFrame({
  'label': ['1:2 Year Return'],
})).mark_text(
    align='center',
    baseline='middle',
    fontSize=10,
    font="Courier New",
    angle=0,  # Adjust the angle if needed
    dx=-250,  # Adjust horizontal offset if needed
    dy=-120,  # Adjust vertical offset if needed
).encode(
  text=alt.Text('label:N'),
)

# Configure the x-axis of the combined chart to display only the first of the month
combined_chart = (area2 + mean + year_2023 + rule + text).properties(width=600).interactive()
combined_chart

alt.LayerChart(...)

In [18]:
flow2 = pd.read_csv('data/cap_flows.csv')
flow2['date'] = pd.to_datetime(flow2['date'])
flow2.set_index('date', inplace=True)
monthly_mean = flow2.resample('M').mean()
monthly_mean.reset_index(inplace=True)
monthly_mean['year'] = pd.DatetimeIndex(monthly_mean['date']).year


In [19]:
flow3 = flow[flow['month'] > 4]
flow4 = flow3[flow3['month'] < 11]


In [20]:
yr_2023 = monthly_mean.loc[monthly_mean['year'] == 2023]


The plot below shows average monthly inflows for the Capilano River above Lakehead (08GA010) gauge (green ticks). You will also see a boxplot showing monthly statistics (1998-2023). The boxplot shows median values, first and third quartiles, the range of max and min, and outliers (circles).     

In [21]:
title = alt.TitleParams(
   text='Capilano River at Lakehead (08GA010)',
   subtitle="Average Monthly Inflows",
   anchor='middle',
   fontSize=14,
   fontWeight='bold')

plot_2023 = alt.Chart(yr_2023).mark_tick(size=14, thickness=3, color='green').encode(
    alt.X('month(date):O'),
    alt.Y('flow:Q'),
    tooltip=[alt.Tooltip('date', title='Date'), alt.Tooltip('flow', title='Inflow')]
)

boxplot = alt.Chart(monthly_mean, title=title).mark_boxplot(opacity=0.7).encode(
    alt.X('month(date):O', title=' '),
    alt.Y('flow:Q', title='River Inflow (m^3/s)')
)
plots = boxplot + plot_2023
plots.properties(width=600, height=200)

alt.LayerChart(...)